In [2]:
from azureml.opendatasets import NycTlcYellow

data = NycTlcYellow()
data_df = data.to_spark_dataframe()
# Display 10 rows
display(data_df.limit(10))

In [3]:
sc.version

'2.4.4.2.6.99.201-22124361'

In [3]:
display(data_df)

In [4]:
#import org.apache.spark.sql.SaveMode
#from pyspark.sql._ import *
from pyspark.sql.functions import *
from pyspark.sql import *
#import org.apache.spark.sql._ 
#import org.apache.spark.sql.functions._

In [5]:
df1 = data_df.withColumn("Date", (col("tpepPickupDateTime").cast("date"))) 
display(df1)

In [12]:
display(df1)

In [6]:
df1.createOrReplaceTempView("nycyellow")

In [15]:
df1.count()

538036931

In [ ]:
df1.dropDuplicates("key","pickup_datetime","pickup_longitude","pickup_latitude","dropoff_longitude","dropoff_latitude")

In [7]:
df1.printSchema

<bound method DataFrame.printSchema of DataFrame[vendorID: string, tpepPickupDateTime: timestamp, tpepDropoffDateTime: timestamp, passengerCount: int, tripDistance: double, puLocationId: string, doLocationId: string, startLon: double, startLat: double, endLon: double, endLat: double, rateCodeId: int, storeAndFwdFlag: string, paymentType: string, fareAmount: double, extra: double, mtaTax: double, improvementSurcharge: string, tipAmount: double, tollsAmount: double, totalAmount: double, puYear: int, puMonth: int, Date: date]>

In [6]:
df2 = df1.withColumn("year", year(col("date"))) .withColumn("month", month(col("date"))) .withColumn("day", dayofmonth(col("date"))) .withColumn("hour", hour(col("date")))

In [7]:
display(df2)

In [8]:
df2.groupBy("year","month").agg(sum("fareAmount").alias("Total"),count("vendorID").alias("Count")).sort(asc("year"), asc("month")).show()

+----+-----+--------------------+--------+
|year|month|               Total|   Count|
+----+-----+--------------------+--------+
|2015|    1| 1.517850853400569E8|12748986|
|2015|    2|1.5384362350999692E8|12450521|
|2015|    3|1.6968078410000235E8|13351609|
|2015|    4| 1.683193264300015E8|13071789|
|2015|    5|1.7459413506000122E8|13158262|
|2015|    6| 1.627394873199964E8|12324935|
|2015|    7| 1.505831559199981E8|11562783|
|2015|    8|1.4516452832999688E8|11130304|
|2015|    9|1.4935045598999912E8|11225063|
|2015|   10|1.6380820285999906E8|12315488|
|2015|   11|1.4891946008999756E8|11312676|
|2015|   12|1.5173508600999984E8|11460573|
|2016|    1|1.3619316658999777E8|10906858|
|2016|    2|1.4129828198999807E8|11382049|
|2016|    3|1.5624008877000007E8|12210952|
|2016|    4|1.5442225344999582E8|11934338|
|2016|    5|1.5791145919000053E8|11836853|
|2016|    6|1.5040771146999735E8|11135470|
|2016|    7|1.3764132431999895E8|10294080|
|2016|    8|1.3178861610999882E8| 9942263|
+----+-----

In [8]:
dfgrouped = df2.groupBy("year","month").agg(sum("fareAmount").alias("Total"),count("vendorID").alias("Count")).sort(asc("year"), asc("month"))

In [9]:
display(dfgrouped)

In [16]:
dfgrouped.repartition(1).write.parquet("/dailyaggr/parquet/dailyaggr.parquet")

In [18]:
dfgrouped.repartition(1).write.option("header","true").csv("/dailyaggrcsv/csv/dailyaggr.csv")

In [12]:
df2.createOrReplaceTempView("nycyellow")

In [13]:
%%sql
select * from nycyellow limit 100

In [14]:
%%sql
select  year(cast(tpepPickupDateTime  as timestamp)) as tsYear,
        month(cast(tpepPickupDateTime  as timestamp)) as tsmonth,
        day(cast(tpepPickupDateTime  as timestamp)) as tsDay, 
        hour(cast(tpepPickupDateTime  as timestamp)) as tsHour,
        avg(totalAmount) as avgTotal, avg(fareAmount) as avgFare
from nycyellow
group by  tsYear, tsmonth,tsDay, tsHour
order by  tsYear, tsmonth,tsDay, tsHour

In [27]:
%%sql
DROP TABLE dailyaggr

In [33]:
%%sql
CREATE TABLE dailyaggr
  COMMENT 'This table is created with existing data'
  AS select  year(cast(tpepPickupDateTime  as timestamp)) as tsYear,
        month(cast(tpepPickupDateTime  as timestamp)) as tsmonth,
        day(cast(tpepPickupDateTime  as timestamp)) as tsDay, 
        hour(cast(tpepPickupDateTime  as timestamp)) as tsHour,
        avg(totalAmount) as avgTotal, avg(fareAmount) as avgFare
from nycyellow
group by  tsYear, tsmonth,tsDay, tsHour
order by  tsYear, tsmonth,tsDay, tsHour

In [12]:
%%sql
select * from dailyaggr

In [13]:
dailyaggr = spark.sql("SELECT tsYear, tsMonth, tsDay, tsHour, avgTotal FROM dailyaggr")

In [14]:
display(dailyaggr)

In [15]:
dailyaggr.write.sqlanalytics("accsynapsepools.wwi.dailyaggr", Constants.INTERNAL)

AttributeError: 'DataFrameWriter' object has no attribute 'sqlanalytics'

In [37]:
from pyspark.ml.regression import LinearRegression

In [38]:
%%pyspark 
import pyspark 
print(print(pyspark.__version__))

2.4.5
None

In [16]:
%%spark
import org.apache.spark.ml.feature.VectorAssembler 
import org.apache.spark.ml.linalg.Vectors 
val dailyaggr = spark.sql("SELECT tsYear, tsMonth, tsDay, tsHour, avgTotal FROM dailyaggr")
val featureCols=Array("tsYear","tsMonth","tsDay","tsHour") 
val assembler: org.apache.spark.ml.feature.VectorAssembler= new VectorAssembler().setInputCols(featureCols).setOutputCol("features") 
val assembledDF = assembler.setHandleInvalid("skip").transform(dailyaggr) 
val assembledFinalDF = assembledDF.select("avgTotal","features")

import org.apache.spark.ml.feature.VectorAssembler
import org.apache.spark.ml.linalg.Vectors
dailyaggr: org.apache.spark.sql.DataFrame = [tsYear: int, tsMonth: int ... 3 more fields]
featureCols: Array[String] = Array(tsYear, tsMonth, tsDay, tsHour)
assembler: org.apache.spark.ml.feature.VectorAssembler = vecAssembler_d7e5f12b687e
assembledDF: org.apache.spark.sql.DataFrame = [tsYear: int, tsMonth: int ... 4 more fields]
assembledFinalDF: org.apache.spark.sql.DataFrame = [avgTotal: double, features: vector]

In [20]:
%%spark
import com.microsoft.spark.sqlanalytics.utils.Constants
import org.apache.spark.sql.SqlAnalyticsConnector._

import com.microsoft.spark.sqlanalytics.utils.Constants
import org.apache.spark.sql.SqlAnalyticsConnector._

In [23]:
%%spark
dailyaggr.repartition(2).write.sqlanalytics("accsynapsepools.wwi.dailyaggr", Constants.INTERNAL)

In [43]:
%%spark
import org.apache.spark.ml.feature.Normalizer 
val normalizedDF = new Normalizer().setInputCol("features").setOutputCol("normalizedFeatures").transform(assembledFinalDF)

import org.apache.spark.ml.feature.Normalizer
normalizedDF: org.apache.spark.sql.DataFrame = [avgTotal: double, features: vector ... 1 more field]

In [44]:
%%spark
val normalizedDF1 = normalizedDF.na.drop()

normalizedDF1: org.apache.spark.sql.DataFrame = [avgTotal: double, features: vector ... 1 more field]

In [45]:
%%spark
val Array(trainingDS, testDS) = normalizedDF1.randomSplit(Array(0.7, 0.3))

trainingDS: org.apache.spark.sql.Dataset[org.apache.spark.sql.Row] = [avgTotal: double, features: vector ... 1 more field]
testDS: org.apache.spark.sql.Dataset[org.apache.spark.sql.Row] = [avgTotal: double, features: vector ... 1 more field]

In [49]:
%%spark
import org.apache.spark.ml.regression.LinearRegression
// Create a LinearRegression instance. This instance is an Estimator. 
val lr = new LinearRegression().setLabelCol("avgTotal").setMaxIter(100)
// Print out the parameters, documentation, and any default values. println(s"Linear Regression parameters:\n ${lr.explainParams()}\n") 
// Learn a Linear Regression model. This uses the parameters stored in lr.
val lrModel = lr.fit(trainingDS)
// Make predictions on test data using the Transformer.transform() method.
// LinearRegression.transform will only use the 'features' column. 
val lrPredictions = lrModel.transform(testDS)

import org.apache.spark.ml.regression.LinearRegression
lr: org.apache.spark.ml.regression.LinearRegression = linReg_e204d6325cfe
lrModel: org.apache.spark.ml.regression.LinearRegressionModel = linReg_e204d6325cfe
lrPredictions: org.apache.spark.sql.DataFrame = [avgTotal: double, features: vector ... 2 more fields]

In [51]:
%%spark
import org.apache.spark.sql.functions._ 
import org.apache.spark.sql.types._ 
println("\nPredictions : " ) 
lrPredictions.select($"avgTotal".cast(IntegerType),$"prediction".cast(IntegerType)).orderBy(abs($"prediction"-$"avgTotal")).distinct.show(15)

import org.apache.spark.sql.functions._
import org.apache.spark.sql.types._

Predictions : 
+--------+----------+
|avgTotal|prediction|
+--------+----------+
|      24|        17|
|      15|        15|
|      18|        16|
|      12|        17|
|      23|        17|
|       6|        17|
|      14|        16|
|     333|        17|
|      37|        17|
|      38|        17|
|      16|        15|
|      13|        15|
|      14|        15|
|      23|        16|
|      28|        18|
+--------+----------+
only showing top 15 rows

In [54]:
%%spark
import org.apache.spark.ml.evaluation.RegressionEvaluator 

val evaluator_r2 = new RegressionEvaluator().setPredictionCol("prediction").setLabelCol("avgTotal").setMetricName("r2") 
//As the name implies, isLargerBetter returns if a larger value is better or smaller for evaluation. 
val isLargerBetter : Boolean = evaluator_r2.isLargerBetter 
println("Coefficient of determination = " + evaluator_r2.evaluate(lrPredictions))

import org.apache.spark.ml.evaluation.RegressionEvaluator
evaluator_r2: org.apache.spark.ml.evaluation.RegressionEvaluator = regEval_33cd6886a1c6
isLargerBetter: Boolean = true
Coefficient of determination = 0.022631234542062728

In [55]:
%%spark
//Evaluate the results. Calculate Root Mean Square Error 
val evaluator_rmse = new RegressionEvaluator().setPredictionCol("prediction").setLabelCol("avgTotal").setMetricName("rmse") 
//As the name implies, isLargerBetter returns if a larger value is better for evaluation. 
val isLargerBetter1 : Boolean = evaluator_rmse.isLargerBetter 
println("Root Mean Square Error = " + evaluator_rmse.evaluate(lrPredictions))

evaluator_rmse: org.apache.spark.ml.evaluation.RegressionEvaluator = regEval_b5343198ec87
isLargerBetter1: Boolean = false
Root Mean Square Error = 4.349077319041537

In [26]:
%%spark
val dailyaggrdf = spark.read.sqlanalytics("accsynapsepools.wwi.dailyaggr")

dailyaggrdf: org.apache.spark.sql.DataFrame = [tsYear: int, tsMonth: int ... 3 more fields]

In [27]:
%%spark
display(dailyaggrdf)

In [28]:
%%spark
dailyaggrdf.count()

res7: Long = 39524